# Imports

In [80]:
from __future__ import division, print_function, absolute_import, unicode_literals
from IPython.core.debugger import set_trace

import cvxpy as cp
import networkx as nx
import io
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import pickle as pk
from time import time
from typing import Text
import tensorflow as tf
from sklearn.model_selection import train_test_split

import sys
sys.path.insert(0, '../src/')
import os.path
from os import path
import utils
import text_processor
import broadcast_network_extraction
from mytimer import Timer

# Parameters

In [81]:
ERROR_TYPE_STR = 'mse'
LAMBDAA = 2
LAMBDAAS = [.1, .2, .5, 1, 2, 5]
RUNS = 10
TEST_FRACTION = 0.2

In [82]:
net_extractor = broadcast_network_extraction.NetworkExtraction()
content_fixer = text_processor.FormalEnglishTranslator('../bagofwords/slang.txt')

In [83]:
directory = '/home/koasato/Documents/research/Jeopardy/'
data = None
try:
    data = utils.load_it(directory + 'Teams_logs.pk')
except:
    print("ERROR")

print(len(data))

49


In [84]:
print(data[42].member_influences)

[[[25, 25, 25, 25], [25, 25, 25, 25], [25, 25, 25, 25], [25, 25, 25, 25]], [[25, 25, 25, 25], [20, 40, 20, 20], [20, 30, 20, 30], [25, 25, 25, 25]], [[25, 25, 25, 25], [33, 34, 33, 33], [20, 30, 20, 30], [25, 25, 25, 25]], [[25, 25, 25, 25], [34, 33, 33, 33], [20, 20, 20, 40], [25, 25, 25, 25]], [[25, 25, 25, 25], [25, 25, 25, 25], [20, 30, 20, 30], [30, 10, 30, 30]], [[25, 25, 25, 25], [25, 25, 25, 25], [15, 50, 15, 20], [25, 25, 25, 25]], [[25, 25, 25, 25], [25, 25, 25, 25], [15, 50, 15, 20], [25, 25, 25, 25]], [[25, 25, 25, 25], [25, 25, 25, 25], [15, 50, 20, 15], [30, 10, 30, 30]], [[100, 0, 0, 0], [25, 25, 25, 25], [20, 40, 20, 20], [30, 10, 30, 30]]]


In [85]:
combined_logs = {}
for team_id, team_log in data.items():
    print("Processing team", team_id, '...')
    this_team_nets = []
    this_team_number_of_networks = min(
        len(team_log.messages) // 5,
        len(team_log.member_influences))
    all_messages_before_appraisal_reports = []
    for i in range(this_team_number_of_networks):
        all_messages_before_appraisal_reports.append(
            pd.concat(
                [team_log.messages[i] for i in np.arange(i * 5, i * 5 + 5)]))
    if len(all_messages_before_appraisal_reports) > 0:
        combined_logs[team_id] = all_messages_before_appraisal_reports
    else:
        print('Team', team_id, 'does not have enough logs.')

Processing team 7 ...
Processing team 10 ...
Processing team 11 ...
Processing team 12 ...
Processing team 13 ...
Processing team 14 ...
Processing team 15 ...
Processing team 16 ...
Processing team 17 ...
Processing team 19 ...
Processing team 20 ...
Processing team 21 ...
Processing team 22 ...
Processing team 23 ...
Processing team 27 ...
Processing team 28 ...
Processing team 30 ...
Processing team 31 ...
Processing team 32 ...
Processing team 33 ...
Processing team 34 ...
Processing team 35 ...
Team 35 does not have enough logs.
Processing team 36 ...
Processing team 37 ...
Processing team 38 ...
Processing team 39 ...
Processing team 40 ...
Processing team 41 ...
Processing team 42 ...
Processing team 43 ...
Processing team 44 ...
Processing team 45 ...
Processing team 46 ...
Processing team 47 ...
Processing team 48 ...
Processing team 49 ...
Processing team 70 ...
Processing team 71 ...
Processing team 72 ...
Team 72 does not have enough logs.
Processing team 73 ...
Team 73 doe

In [ ]:
size = 20
GAMMAS = [.1, .2, .5, 1, 2, 5]
with Timer():
    for lambdaa in LAMBDAAS:
        for gamma in GAMMAS:
            print("running with lambdaa = ", lambdaa)
            print("running with gamma = ", gamma)
            mean_total_error = np.zeros(shape=(size,size))
            std_total_error = np.zeros(shape=(size,size))
            model_errs = []
            error_file_name = directory+'Time_Window_Error_mse_lambda' + str(lambdaa) + '_gamma' + str(gamma) + '.pk'
            std_file_name = directory+'Time_Window_Std_mse_lambda' + str(lambdaa) + '_gamma' + str(gamma) + '.pk'
            if (path.exists(error_file_name) or path.exists(std_file_name)):
                print(error_file_name + " already exists")
                continue
            for b in range(0, size):
                for e in range(0, size):
                    if b >= e:
                        continue
                    time_window = [b, e]
                    cumulative_mse_for_time_window = 0
                    counter = 0

                    X = []
                    y = []
                    print("time window = ", time_window)
                    for team_id, all_messages_before_appraisal_reports in combined_logs.items():
                        members = data[team_id].members
                        print("Processing team", team_id, '...')
                        this_team_nets = []

                        for index, all_messages_before_appraisal_report in enumerate(all_messages_before_appraisal_reports):
                            reply_duration_net = net_extractor.extract_network_from_broadcast(            
                                communication_data=all_messages_before_appraisal_report,
                                time_window=time_window,
                                weight_type=broadcast_network_extraction.WeightType.REPLY_DURATION,
                                aggregation_type=broadcast_network_extraction.AggregationType.SUM,
                                gamma=gamma,
                                node_list=members)
                            influence_matrix = np.matrix(data[team_id].member_influences[index])
                            to_be_predicted_influence_matrix = utils.shuffle_matrix_in_given_order(
                                    matrix=influence_matrix,
                                    order=np.argsort(members)) / 100
                            # Use reply_duration_net to predict to_be_predicted_influence_matrix
                            reply_duration_net_matrix = nx.adj_matrix(reply_duration_net).todense()

                            X.append(reply_duration_net_matrix)
                            y.append(to_be_predicted_influence_matrix)

                    model_err = []
                    for run in range(RUNS):
                        X_train, X_test, y_train, y_test = train_test_split(
                            X, y, test_size=TEST_FRACTION)

                        # Solving the optimization problem.
                        W = cp.Variable((4, 4))
                        B = cp.Variable((4, 4))

                        constraints = []
                        losses = 0
                        for index in range(len(X_train)):
                            A = X_train[index]
                            influence_matrix = y_train[index]
                            pred_influence_matrix = A * W + B

                            if (ERROR_TYPE_STR == 'mse'):
                                losses += cp.sum_squares(pred_influence_matrix - influence_matrix)
                            else:
                                raise ValueError("Incorrect ERROR_TYPE_STR")

                            constraints += [pred_influence_matrix >= 0]
                            constraints += [cp.sum(pred_influence_matrix, axis=1) == 1]
                        regluarization = cp.norm1(W) + cp.norm1(B)
                        objective = cp.Minimize(losses + lambdaa * regluarization)
                        prob = cp.Problem(objective, constraints)
                        try:
                            result = prob.solve()
                        except cp.SolverError as e:
                            print('Problem was not solved for lambda: {}'.format(lambdaa))
            #                 return sys.maxsize, sys.maxsize
                        print('The status of solution was: {} and the result was: {}'.format(prob.status, result))

                        model_err = 0
                        for index in range(len(X_test)):
                            A = X_test[index]
                            influence_matrix = y_test[index]
                            # Optimization model prediction:
                            predicted_influence_matrix = (A * W.value + B.value)
                            model_err += utils.matrix_estimation_error(
                                influence_matrix, predicted_influence_matrix, type_str=ERROR_TYPE_STR)
                        model_errs.append(model_err)

                    mean_total_error[b][e] = np.mean(model_errs)
                    std_total_error[b][e] = np.std(model_errs)
            utils.save_it(mean_total_error, error_file_name, verbose=True)
            utils.save_it(std_total_error, std_file_name, verbose=True)

running with lambdaa =  0.1
running with gamma =  0.1
time window =  [0, 1]
Processing team 7 ...
Processing team 10 ...
Processing team 11 ...
Processing team 12 ...
Processing team 13 ...
Processing team 14 ...
Processing team 15 ...
Processing team 16 ...
Processing team 17 ...
Processing team 19 ...
Processing team 20 ...
Processing team 21 ...
Processing team 22 ...
Processing team 23 ...
Processing team 27 ...
Processing team 28 ...
Processing team 30 ...
Processing team 31 ...
Processing team 32 ...
Processing team 33 ...
Processing team 34 ...
Processing team 36 ...
Processing team 37 ...
Processing team 38 ...
Processing team 39 ...
Processing team 40 ...
Processing team 41 ...
Processing team 42 ...
Processing team 43 ...
Processing team 44 ...
Processing team 45 ...
Processing team 46 ...
Processing team 47 ...
Processing team 48 ...
Processing team 49 ...
Processing team 70 ...
Processing team 71 ...
Processing team 74 ...
Processing team 75 ...
Processing team 77 ...
Proce

Processing team 75 ...
Processing team 77 ...
Processing team 79 ...
Processing team 82 ...
Processing team 84 ...
Processing team 85 ...
Processing team 87 ...
Processing team 88 ...
The status of solution was: optimal and the result was: 52.885059005236705
The status of solution was: optimal and the result was: 52.21523469635604
The status of solution was: optimal and the result was: 53.99049608405634
The status of solution was: optimal and the result was: 52.54322538039417
The status of solution was: optimal and the result was: 57.596307081980115
The status of solution was: optimal and the result was: 53.90308221142936
The status of solution was: optimal and the result was: 53.99256171875257
The status of solution was: optimal and the result was: 55.90798233085705
The status of solution was: optimal and the result was: 55.53964571769096
The status of solution was: optimal and the result was: 55.42837808204183
time window =  [0, 6]
Processing team 7 ...
Processing team 10 ...
Process

Processing team 11 ...
Processing team 12 ...
Processing team 13 ...
Processing team 14 ...
Processing team 15 ...
Processing team 16 ...
Processing team 17 ...
Processing team 19 ...
Processing team 20 ...
Processing team 21 ...
Processing team 22 ...
Processing team 23 ...
Processing team 27 ...
Processing team 28 ...
Processing team 30 ...
Processing team 31 ...
Processing team 32 ...
Processing team 33 ...
Processing team 34 ...
Processing team 36 ...
Processing team 37 ...
Processing team 38 ...
Processing team 39 ...
Processing team 40 ...
Processing team 41 ...
Processing team 42 ...
Processing team 43 ...
Processing team 44 ...
Processing team 45 ...
Processing team 46 ...
Processing team 47 ...
Processing team 48 ...
Processing team 49 ...
Processing team 70 ...
Processing team 71 ...
Processing team 74 ...
Processing team 75 ...
Processing team 77 ...
Processing team 79 ...
Processing team 82 ...
Processing team 84 ...
Processing team 85 ...
Processing team 87 ...
Processing 

Processing team 84 ...
Processing team 85 ...
Processing team 87 ...
Processing team 88 ...
The status of solution was: optimal and the result was: 52.1475994321987
The status of solution was: optimal and the result was: 54.01701637931084
The status of solution was: optimal and the result was: 54.968687723965765
The status of solution was: optimal and the result was: 53.25681435923561
The status of solution was: optimal and the result was: 55.640495569931254
The status of solution was: optimal and the result was: 51.00356086311279
The status of solution was: optimal and the result was: 54.47927290353873
The status of solution was: optimal and the result was: 53.2710716092164
The status of solution was: optimal and the result was: 52.58319217056941
The status of solution was: optimal and the result was: 54.86594277344838
time window =  [0, 15]
Processing team 7 ...
Processing team 10 ...
Processing team 11 ...
Processing team 12 ...
Processing team 13 ...
Processing team 14 ...
Processi

Processing team 12 ...
Processing team 13 ...
Processing team 14 ...
Processing team 15 ...
Processing team 16 ...
Processing team 17 ...
Processing team 19 ...
Processing team 20 ...
Processing team 21 ...
Processing team 22 ...
Processing team 23 ...
Processing team 27 ...
Processing team 28 ...
Processing team 30 ...
Processing team 31 ...
Processing team 32 ...
Processing team 33 ...
Processing team 34 ...
Processing team 36 ...
Processing team 37 ...
Processing team 38 ...
Processing team 39 ...
Processing team 40 ...
Processing team 41 ...
Processing team 42 ...
Processing team 43 ...
Processing team 44 ...
Processing team 45 ...
Processing team 46 ...
Processing team 47 ...
Processing team 48 ...
Processing team 49 ...
Processing team 70 ...
Processing team 71 ...
Processing team 74 ...
Processing team 75 ...
Processing team 77 ...
Processing team 79 ...
Processing team 82 ...
Processing team 84 ...
Processing team 85 ...
Processing team 87 ...
Processing team 88 ...
The status 

...

Processing team 30 ...
Processing team 31 ...
Processing team 32 ...
Processing team 33 ...
Processing team 34 ...
Processing team 36 ...
Processing team 37 ...
Processing team 38 ...
Processing team 39 ...
Processing team 40 ...
Processing team 41 ...
Processing team 42 ...
Processing team 43 ...
Processing team 44 ...
Processing team 45 ...
Processing team 46 ...
Processing team 47 ...
Processing team 48 ...
Processing team 49 ...
Processing team 70 ...
Processing team 71 ...
Processing team 74 ...
Processing team 75 ...
Processing team 77 ...
Processing team 79 ...
Processing team 82 ...
Processing team 84 ...
Processing team 85 ...
Processing team 87 ...
Processing team 88 ...
The status of solution was: optimal and the result was: 56.534452622552756
The status of solution was: optimal and the result was: 57.34292769223398
The status of solution was: optimal and the result was: 55.671349452128055
The status of solution was: optimal and the result was: 58.19700381635608
The status o

The status of solution was: optimal and the result was: 58.58920460588122
The status of solution was: optimal and the result was: 58.68345522594138
The status of solution was: optimal and the result was: 55.79964701522913
The status of solution was: optimal and the result was: 56.70004795640404
The status of solution was: optimal and the result was: 57.435890506393015
The status of solution was: optimal and the result was: 58.46179247495553
The status of solution was: optimal and the result was: 58.972939853061085
time window =  [3, 17]
Processing team 7 ...
Processing team 10 ...
Processing team 11 ...
Processing team 12 ...
Processing team 13 ...
Processing team 14 ...
Processing team 15 ...
Processing team 16 ...
Processing team 17 ...
Processing team 19 ...
Processing team 20 ...
Processing team 21 ...
Processing team 22 ...
Processing team 23 ...
Processing team 27 ...
Processing team 28 ...
Processing team 30 ...
Processing team 31 ...
Processing team 32 ...
Processing team 33 ..

Processing team 30 ...
Processing team 31 ...
Processing team 32 ...
Processing team 33 ...
Processing team 34 ...
Processing team 36 ...
Processing team 37 ...
Processing team 38 ...
Processing team 39 ...
Processing team 40 ...
Processing team 41 ...
Processing team 42 ...
Processing team 43 ...
Processing team 44 ...
Processing team 45 ...
Processing team 46 ...
Processing team 47 ...
Processing team 48 ...
Processing team 49 ...
Processing team 70 ...
Processing team 71 ...
Processing team 74 ...
Processing team 75 ...
Processing team 77 ...
Processing team 79 ...
Processing team 82 ...
Processing team 84 ...
Processing team 85 ...
Processing team 87 ...
Processing team 88 ...
The status of solution was: optimal and the result was: 59.3001289731485
The status of solution was: optimal and the result was: 59.7589980325437
The status of solution was: optimal and the result was: 55.99715525404529
The status of solution was: optimal and the result was: 57.79970889880154
The status of so

The status of solution was: optimal and the result was: 56.458812126679376
The status of solution was: optimal and the result was: 59.41356766304071
The status of solution was: optimal and the result was: 58.71361326766267
The status of solution was: optimal and the result was: 58.486449757715825
The status of solution was: optimal and the result was: 56.51998557400454
The status of solution was: optimal and the result was: 59.44953814941479
The status of solution was: optimal and the result was: 59.08371714141096
time window =  [4, 11]
Processing team 7 ...
Processing team 10 ...
Processing team 11 ...
Processing team 12 ...
Processing team 13 ...
Processing team 14 ...
Processing team 15 ...
Processing team 16 ...
Processing team 17 ...
Processing team 19 ...
Processing team 20 ...
Processing team 21 ...
Processing team 22 ...
Processing team 23 ...
Processing team 27 ...
Processing team 28 ...
Processing team 30 ...
Processing team 31 ...
Processing team 32 ...
Processing team 33 ..

Processing team 30 ...
Processing team 31 ...
Processing team 32 ...
Processing team 33 ...
Processing team 34 ...
Processing team 36 ...
Processing team 37 ...
Processing team 38 ...
Processing team 39 ...
Processing team 40 ...
Processing team 41 ...
Processing team 42 ...
Processing team 43 ...
Processing team 44 ...
Processing team 45 ...
Processing team 46 ...
Processing team 47 ...
Processing team 48 ...
Processing team 49 ...
Processing team 70 ...
Processing team 71 ...
Processing team 74 ...
Processing team 75 ...
Processing team 77 ...
Processing team 79 ...
Processing team 82 ...
Processing team 84 ...
Processing team 85 ...
Processing team 87 ...
Processing team 88 ...
The status of solution was: optimal and the result was: 60.1788384602501
The status of solution was: optimal and the result was: 56.759888518385736
The status of solution was: optimal and the result was: 56.959308934467614
The status of solution was: optimal and the result was: 56.74789763598481
The status of

In [ ]:
# utils.save_it(mean_total_error, directory+'Time_Window_Error_mse_lambda2_gamma2.pk', verbose=True)
# utils.save_it(std_total_error, directory+'Time_Window_Std_mse_lambda2_gamma2.pk', verbose=True)

In [ ]:
# mean_total_error = utils.load_it(directory+'Time_Window_Error_mse_lambda0.1_gamma0.1.pk',verbose=True)
# std_total_error = utils.load_it(directory+'Time_Window_Std_mse_lambda0.1_gamma0.1.pk',verbose=True)


In [ ]:
print(mean_total_error)

In [ ]:
print(std_total_error)

In [ ]:
# mean_total_error[mean_total_error == .0] = .9
import seaborn as sns
import matplotlib.pylab as plt
sns.heatmap(mean_total_error)
plt.show()

In [ ]:
np.min(mean_total_error)

In [ ]:
np.where(mean_total_error == np.min(mean_total_error))

In [ ]:
### best window for mse = 4,5
# best window for cosine = 0,2
# best window for normalized = 0, 1
# best window for cosine_0.01 = 0, 5

# best window for mse gamma 0.3 lambda 0.1 = 0,1
# best window for mse gamma 0.5 lambda 0.1 = 0,1
# best window for mse gamma 1 lambda 0.1 = 7, 22
# best window for mse gamma 3 lambda 0.1 = 0, 2
# best window for mse gamma 5 lambda 0.1 = 0, 1
# best window for mse gamma 10 lambda 0.1 = 0, 1

# best window for mse gamma 0.5 lambda 0.5 = 0, 2
# best window for mse gamma 0.5 lambda 1 = 0, 1
# best window for mse gamma 0.5 lambda 2 = 0, 5
# best window for mse gamma 0.5 lambda 5 = 0, 9

# best window for mse gamma 1 lambda 0.5 = 0, 5
# best window for mse gamma 1 lambda 1 = 0, 9
# best window for mse gamma 1 lambda 2 = 0, 9
# best window for mse gamma 1 lambda 5 = 0, 19

# best window for mse gamma 2 lambda .1 = 3,4
# best window for mse gamma 2 lambda .5 = 0,8
# best window for mse gamma 2 lambda 1 = 0,1
# best window for mse gamma 2 lambda 2 = 0, 7
